# Начинаем работу...  

Необходимо развернуть и запустить проект по реализации обучения с подкреплением для игры "Крестики-нолики"  

Перевести проект на библиотеку gymnasium и современную версию Python. Реализовать агена для игры "Крестики-нолики" ы ымдк отдельного класса (как в лекции). Переписать основной цикл обучения для работы с отдельным классом агента (как в лекции). Протестировать новую версию программы.  

**Обучение с подкреплением** (Reinforcement Learning, RL) — это метод машинного обучения, при котором агент обучается путем взаимодействия с окружающей средой. Цель агента — максимизировать получаемую награду через последовательность действий.



Крестики-нолики: https://github.com/nczempin/gym-tic-tac-toe

## Перевод среды на Gymnasium  

**Gymnasium (ранее OpenAI Gym)** — это библиотека для создания и тестирования алгоритмов обучения с подкреплением. Она предоставляет набор стандартных сред для RL, таких как игры, задачи управления и симуляции.  

Gymnasium предлагает обновленную API по сравнению с Gym:  
Упростились методы reset и step. Добавлены новые возможности, такие как поддержка тайм-аутов и контроль шагов. Улучшена поддержка пользовательских сред.  

*Основные возможности Gymnasium:*  
Стандартизированные интерфейсы для взаимодействия со средой. Простая интеграция с популярными библиотеками RL. Поддержка пользовательских сред.  

*Ключевые функции Gymnasium:*  
env.reset() — инициализация среды.  
env.step(action) — выполнение действия и переход в новое состояние.  
env.render() — визуализация текущего состояния среды.  

In [4]:
import gymnasium as gym
from gymnasium import spaces

class TicTacToeEnv(gym.Env):
    metadata = {'render.modes': ['human']}
    
    symbols = ['O', ' ', 'X']

    def __init__(self):
        super().__init__()
        self.action_space = spaces.Discrete(9)
        self.observation_space = spaces.Discrete(9 * 3 * 2)
        self.reset()

    def step(self, action):
        done = False
        reward = 0

        p, square = action  # p - игрок (1 или -1), square - номер клетки

        board = self.state['board']
        proposed = board[square] 
        om = self.state['on_move'] 
        if proposed != 0:  # Клетка уже занята
            print(f"Незаконный ход: Квадрат {square} уже занят.")
            done = True
            reward = -1 * om 
        if p != om:  # Не тот игрок на ходу
            print(f"Незаконный ход: игрок {p} не находится в движении")
            done = True
            reward = -1 * om
        else:
            board[square] = p
            self.state['on_move'] = -p

        for i in range(3):
            # Горизонтали и вертикали
            if (board[i * 3] == p and board[i * 3 + 1] == p and board[i * 3 + 2] == p) or \
               (board[i] == p and board[i + 3] == p and board[i + 6] == p):
                reward = p
                done = True
                break

        # Диагонали
        if (board[0] == p and board[4] == p and board[8] == p) or \
           (board[2] == p and board[4] == p and board[6] == p):
            reward = p
            done = True
                
        return self.state, reward, done, {}

    def reset(self):
        self.state = {}
        self.state['board'] = [0, 0, 0, 0, 0, 0, 0, 0, 0] 
        self.state['on_move'] = 1 
        return self.state, {}

    def render(self, close=False):
        if close:
            return
        print("on move: " , self.symbols[self.state['on_move']+1])
        for i in range (9):
            print (self.symbols[self.state['board'][i]+1], end=" ");
            if ((i % 3) == 2):
                print();

    def move_generator(self):
        moves = []
        for i in range(9):
            if self.state['board'][i] == 0:
                p = self.state['on_move']
                m = [p, i]
                moves.append(m)
        return moves

### Реализация агента  

Агент в контексте обучения с подкреплением (Reinforcement Learning, RL) — это система, которая взаимодействует с окружающей средой, чтобы достичь определенной цели. Его задача — выработать стратегию, которая максимизирует получаемую награду в долгосрочной перспективе.  

Роль агента:  
Агент принимает решение (выбирает действие), основываясь на текущем состоянии среды, и затем получает обратную связь (награду и новое состояние) от среды.  

Функционал агента:  
Выбор действия: Использует алгоритмы или стратегии, чтобы определить, что делать дальше.  
Обучение: Обновляет свои знания или стратегию на основе опыта, чтобы лучше справляться с задачей.  
Интерактивность: Адаптируется к изменениям в среде.  

In [5]:
import random

# Реализация Агента, который в рамках обучения с подкреплением взаимодействует со средой и вырабатывает наилучшую стратегию  

class Agent:
    def __init__(self, symbol):
        self.symbol = symbol  # Символ игрока (1 - X, -1 - O)
    
    def get_action(self, moves):
        return random.choice(moves)  # Выбираем случайный ход из доступных

### Основной цикл обучения  

Основной цикл включает в себя создание среды и работу с ней. По истечению выполнения игры, начисляются очки, которые будут свидетельствовать о том, какие результаты достиг наш агент, обучилась ли наша система. 

In [6]:
# Основной цикл обучения (работа с отдельным классом агента)

# Создание среды для игры в крестики-нолики
environment = TicTacToeEnv()

# Создание агента (играющего крестиками)
agent = Agent(symbol=1)

num_episodes = 150  # Количество эпизодов (игр) для обучения
collected_rewards = []      # Список для хранения наград/побед в каждом эпизоде 

# Переменная для отслеживания символа и текущего игрока
oom = 1

for i in range(num_episodes):
    # Сброс среды и начало нового эпизода
    state, _ = environment.reset() 

    # Общая награда за эпизод
    total_reward = 0

    # Флаг завершения игры
    done = False
    om = oom 

    # Максимум 9 ходов, поскольку поле 3x3 
    for j in range(9): 
        moves = environment.move_generator() 

        # Ходов нет, заканчиваем игру
        if not moves:
            break

        
        if len(moves) == 1:
            move = moves[0]    # Если остался один ход на основе стратегии
        else:
            move = agent.get_action(moves)   # Агент выбирает ход на основе стратегии

        # Выполнение хода и обновление состояния игры
        next_state, reward, done, info = environment.step(move)
        total_reward += reward
        state = next_state

        # Отображаем текущее состояние игры
        environment.render()

        if done:
            break

        om = -om    # Смена игрока

    collected_rewards.append(total_reward)

    print(f"Episode {i+1}, Total Reward: {total_reward}")
    average_reward = sum(collected_rewards) / len(collected_rewards)
    print(f"Average Reward: {average_reward}")

on move:  O
  X   
      
      
on move:  X
  X   
    O 
      
on move:  O
  X X 
    O 
      
on move:  X
  X X 
    O 
  O   
on move:  O
  X X 
    O 
X O   
on move:  X
O X X 
    O 
X O   
on move:  O
O X X 
  X O 
X O   
Episode 1, Total Reward: 1
Average Reward: 1.0
on move:  O
X     
      
      
on move:  X
X     
      
    O 
on move:  O
X   X 
      
    O 
on move:  X
X   X 
      
O   O 
on move:  O
X   X 
X     
O   O 
on move:  X
X O X 
X     
O   O 
on move:  O
X O X 
X     
O X O 
on move:  X
X O X 
X O   
O X O 
on move:  O
X O X 
X O X 
O X O 
Episode 2, Total Reward: 0
Average Reward: 0.5
on move:  O
      
      
X     
on move:  X
      
O     
X     
on move:  O
      
O     
X X   
on move:  X
  O   
O     
X X   
on move:  O
  O   
O X   
X X   
on move:  X
  O   
O X   
X X O 
on move:  O
  O X 
O X   
X X O 
Episode 3, Total Reward: 1
Average Reward: 0.6666666666666666
on move:  O
      
  X   
      
on move:  X
O     
  X   
      
on move:  O
O     
